In [1]:
import requests
import re
from bs4 import BeautifulSoup
import json
from multiprocessing import Pool
import time 

import traceback
# import concurrent.futures
# from itertools import repeat


def daily_crawler(Key_work):
    
    domain_name = 'https://www.dice.com'

    ## Input you want
    Key_location =''
    key_main=domain_name+'/jobs/'+'q-'+Key_work+'-l-'+Key_location+'-radius-30-startPage-1-jobs?'

    ## Calculate Job Pages
    response_main = requests.get(key_main)
    soup = BeautifulSoup(response_main.text,'lxml')
    pages = int(str(soup.find("",{"id":"posiCountId"}).text).replace(',',''))//30
    print('Total have '+str(pages)+' pages')

    href = []
    
#     with concurrent.futures.ProcessPoolExecutor(max_workers=70) as executor:
#         href += executor.map(write_into_dict, range(1, pages+1), repeat(domain_name), repeat(Key_work), repeat(Key_location))  
    
    input_data = [ (page, domain_name, Key_work, Key_location) for page in range(1, pages+1) ]
    
    with Pool(processes=70) as pool:
        href += pool.map(write_into_dict, input_data)    
    
    
    href = [ url for page_href in href for url in page_href ]
    print("Total have : ",len(href))
    
    start = time.time()
    with Pool(processes=70) as pool:
        contents = pool.map(fetch_article_content, href)

    end = time.time()
    print(end-start, "sec")
    
    result = load_to_json(Key_work, contents)
    print(len(result[Key_work]))
    
    return result
    

## Add all pages's work
def write_into_dict(input_data):
    page, domain_name, Key_work, Key_location = input_data[0], input_data[1], input_data[2], input_data[3]
    response_page = requests.get(domain_name+'/jobs/'+'q-'+Key_work+'-l-'+Key_location+'-radius-30-startPage-'+str(page)+'-jobs?')
    soup1 = BeautifulSoup(response_page.text,'lxml')
    # every page contains 30 urls
    
    page_href = []
    for i in range(30):
        try:
            tmp = domain_name + soup1.find("",{"id":"position"+str(i)}).get('href')
            page_href.append(requests.utils.requote_uri(tmp))
        except:
            print()
            traceback.print_exc()
            print()
            
    if page%30 == 0:
        print('page '+ str(page)+' is finished')
        
    return page_href

def fetch_article_content(url):
    judege  = True
    
    response_work = requests.get(url)
    soup = BeautifulSoup(response_work.text,'lxml')
    if soup.find("",{"class":"pull-left h1 jobs-page-header-h1"}):
        judege = False
    if soup.find("",{"class":"col-md-12 error-page-header"}):
        judege = False
    
    
    if judege==True:
        try:
            
            jobTitle = soup.find("",{"class":"jobTitle"}).text
            
            jobEmployer = soup.find("",{"class":"employer"}).text.replace('\n','').replace('\t','')
            jobLocation = soup.find("",{"class":"location"}).text.replace('\n','')
            jobPostTime = soup.find("",{"class":"posted hidden-xs"}).text
            jobID = soup.find("",{"class":"company-header-info"}).text
            jobID = jobID.replace('\n','').split(':')[2].strip().replace('-','')
            ## tag job-info is a array .
            foo = soup.find_all("",{"class":"row job-info"})

            out = []
            for o in foo:
                out.append(o.text.replace('\n','').replace('\t',''))

        except AttributeError:
            jobTitle='None'
            jobEmployer='None'
            jobLocation='None'
            jobPostTime='None'
            foo='None'
            jobID='None'
            #jobDescription=''   

        try:
            jobskillss = out[0]
            jobemploymentType = out[1]
            jobbaseSalary = out[2]

        except IndexError:
            jobskillss = 'None'
            jobemploymentType = 'None'
            jobbaseSalary = 'None'

    ## Jobdescription
        str1 = str(soup.find("",{"id":"jobdescSec"}))
        soup = BeautifulSoup(str1.replace('<br/>','\n').replace('</li>','\n').replace('</strong>','\n').replace('</p>','\n').replace('<p>','\n'),'lxml')
        jobDescription = soup.text
        joburl = url
    else:
        return
        
    
    return((jobTitle,jobEmployer,jobLocation,jobPostTime,jobID,jobskillss,jobemploymentType,jobbaseSalary,joburl,jobDescription))

def load_to_json(Key_work, content_arry):
    flag=True
    for i in content_arry:
        if i:
            jobTitle = i[0]
            jobEmployer = i[1]
            jobLocation = i[2]
            jobPostTime = i[3]
            jobID = i[4]
            jobskills = i[5]
            jobemploymentType = i[6]
            jobbaseSalary = i[7]
            joburl = i[8]
            jobDescription = i[9]
        
            if flag==True:
                data = {Key_work:[{
                             "jobID":jobID,
                             "jobTitle":jobTitle,
                             "jobEmployer":jobEmployer,
                             "jobLocation":jobLocation,
                             "jobPostTime":jobPostTime,
                             "jobskills":jobskills,
                             "jobemploymentType":jobemploymentType,
                             "jobbaseSalary":jobbaseSalary,
                             "joburl":joburl,
                             "jobDescription":jobDescription,
                                 }]}
                flag=False


            else:
                add_data = {    "jobID":jobID,  
                                "jobTitle":jobTitle,
                                "jobEmployer":jobEmployer,
                                "jobLocation":jobLocation,
                                "jobPostTime":jobPostTime,
                                "jobskills":jobskills,
                                "jobemploymentType":jobemploymentType,
                                "jobbaseSalary":jobbaseSalary,
                                "joburl":joburl,
                                "jobDescription":jobDescription  }
                data[Key_work].append(add_data)
    return data

In [3]:
%%time
daily_crawler("Frontend")

Total have 129 pages
page 30 is finished
page 60 is finished
page 90 is finished
page 120 is finished
Total have :  3870
100.27598118782043 sec
3870
CPU times: user 791 ms, sys: 565 ms, total: 1.36 s
Wall time: 1min 55s


{'Frontend': [{'jobDescription': "\nTop Requirement: All resumes submitted must contain links to examples of front-end and graphic design work such as websites, marketing banners, headers, logos, etc in order to be considered for this position!\n\n\n***We are only accepting applications from US citizens or those with green cards currently living in the US at this time willing to work full time in our San Diego office. ***\n\n\nTired of working on boring projects?\n\nDo you want to sharpen your skills in a team-based environment?\n\nIf so, here's your chance to be part of a stable company that will provide a great professional work environment, interesting work and strong learning and career growth potential! You will work daily in our San Diego office as this is not a remote opportunity.\n\nWe are looking for someone to help improve visual elements of our websites and applications who can combine the art of design with the art of programming. We need someone to bridge the gap between g

In [2]:
%%time
daily_crawler("Frontend")

AttributeError: 'NoneType' object has no attribute 'text'

In [2]:
%%time
daily_crawler("Backend")

Total have 120 pages
page 30 is finished
page 90 is finished
page 60 is finished
page 120 is finished
Total have :  3600
93.40583276748657 sec
3600
CPU times: user 759 ms, sys: 562 ms, total: 1.32 s
Wall time: 1min 44s


{'Backend': [{'jobDescription': '\nPolySign Senior Back End Engineer\n\n\nAs a Senior Backend Engineer at PolySign you will help architect and build the business logic and backbone services for the PolySign crypto-currency platform. You will build central services such as the account, firm, and vault managers that form the backbone of our system, and connect them to the PolySign front end systems which include web and mobile platforms.\n\nIn this position you will work on a small team with other top talent with a significant impact on both architecture and direction. You will interface with and assist the front end and cloud services teams to help launch our platform.\n\n\nWhat you’ll do:\n\nArchitect and build the PolySign back end working with cloud services team, and front end team to produce a world-class fintech service\nBuild quality in, delivering significant unit, integration and system tests along with your code\nWrite developer documentation, reference implementations, and ot

In [5]:
%%time
daily_crawler("Backend")

AttributeError: 'NoneType' object has no attribute 'text'